## This notebook performs the assessment on the downloaded metadata files

(Running it all the way through takes relatively long (~120h computation time in total on our end))


In [1]:
import requests
import re
import json
import pandas as pd
import numpy as np
import matplotlib.lines as mlines
from itertools import chain
from matplotlib import pyplot as plt

### German data portal assessment

In [2]:
date = "2024-05-26"

In [8]:
df = pd.read_csv(r"C:\Users\MolnarM\Downloads\datasets_metadata.csv")
df.head()

author           author_email  \
0    Hanse- und Universitätsstadt Rostock – Hauptamt  geodienste@rostock.de   
1  Hanse- und Universitätsstadt Rostock – Kataste...  geodienste@rostock.de   
2  Hanse- und Universitätsstadt Rostock – Kataste...  geodienste@rostock.de   
3  Hanse- und Universitätsstadt Rostock – Kataste...  geodienste@rostock.de   
4    Hanse- und Universitätsstadt Rostock – Hauptamt  geodienste@rostock.de   

                        creator_user_id                                    id  \
0  f512f73d-bed2-439d-8f6f-3fbc6048b24e  05be0aa5-76a2-4850-b37f-69e623565fbe   
1  f512f73d-bed2-439d-8f6f-3fbc6048b24e  44fa7d61-7924-4740-95ec-b4a6821139fe   
2  f512f73d-bed2-439d-8f6f-3fbc6048b24e  6219e4c3-e819-40f0-86cd-543ff829ad6c   
3  f512f73d-bed2-439d-8f6f-3fbc6048b24e  7c46a2cc-4fe3-4399-8833-61b016730b71   
4  f512f73d-bed2-439d-8f6f-3fbc6048b24e  4d25536c-7cc4-4761-8504-0ba8ca320fa1   

   isopen  license_id  license_title  \
0   False         NaN            NaN   
1   False         NaN            NaN   
2   False         NaN            NaN   
3   False         NaN            NaN   
4   False         NaN            NaN   

                                          maintainer       maintainer_email  \
0  Hanse- und Universitätsstadt Rostock – Kataste...  geodienste@rostock.de   
1  Hanse- und Universitätsstadt Rostock – Kataste...  geodienste@rostock.de   
2  Hanse- und Universitätsstadt Rostock – Kataste...  geodienste@rostock.de   
3  Hanse- und Universitätsstadt Rostock – Kataste...  geodienste@rostock.de   
4  Hanse- und Universitätsstadt Rostock – Kataste...  geodienste@rostock.de   

             metadata_created  ...                                 title  \
0  2023-01-06T06:14:11.920576  ...                   Bundestagswahl 2013   
1  2024-05-08T06:31:53.940777  ...                  Bodenrichtwerte 2015   
2  2024-05-08T06:31:46.141017  ...                  Bodenrichtwerte 2008   
3  2024-05-08T06:32:00.483952  ...  38. Internationaler Hansetag Rostock   
4  2024-05-08T06:32:18.276436  ...                      Ortsamtsbereiche   

      type                                                url  version  \
0  dataset  https://www.opendata-hro.de/dataset/e7c10dd4-d...      NaN   
1  dataset  https://www.opendata-hro.de/dataset/c276228b-9...      NaN   
2  dataset  https://www.opendata-hro.de/dataset/655f46c2-1...      NaN   
3  dataset  https://www.opendata-hro.de/dataset/7afdfa7a-7...      NaN   
4  dataset  https://www.opendata-hro.de/dataset/aceccfc0-d...      NaN   

                                              extras  \
0  [{'key': 'access_rights', 'value': 'http://pub...   
1  [{'key': 'access_rights', 'value': 'http://pub...   
2  [{'key': 'access_rights', 'value': 'http://pub...   
3  [{'key': 'access_rights', 'value': 'http://pub...   
4  [{'key': 'access_rights', 'value': 'http://pub...   

                                              groups  \
0  [{'description': '', 'display_name': 'Regierun...   
1  [{'description': '', 'display_name': 'Regierun...   
2  [{'description': '', 'display_name': 'Regierun...   
3  [{'description': '', 'display_name': 'Bildung,...   
4  [{'description': '', 'display_name': 'Regierun...   

                                           resources  \
0  [{'access_url': 'https://geo.sv.rostock.de/dow...   
1  [{'access_url': 'https://geo.sv.rostock.de/dow...   
2  [{'access_url': 'https://geo.sv.rostock.de/dow...   
3  [{'access_url': 'https://geo.sv.rostock.de/dow...   
4  [{'access_url': 'https://geo.sv.rostock.de/dow...   

                                                tags relationships_as_subject  \
0  [{'display_name': 'politik', 'id': 'a8e6e4aa-6...                       []   
1  [{'display_name': 'bauleitplanung', 'id': '861...                       []   
2  [{'display_name': 'bauleitplanung', 'id': '861...                       []   
3  [{'display_name': 'freizeit', 'id': '73a5f345-...                       []   
4  [{'display_name': 'behörde', 'id': 'e15183d8-d.

In [14]:
count = 0
assessment_results = df['url'].map(lambda x: get_all_metrics(payload={'url': x}))
df['FAIR_assessment'] = [aresult[0] for aresult in assessment_results]
df['assessment_status_code'] = [aresult[1] for aresult in assessment_results]
df.to_csv(r"C:\Users\MolnarM\Desktop\Notebooks\Uni\ogdmetadatendatagvat_assessed_german"+date+".csv", encoding='utf-8')
df

0
{'url': 'https://www.opendata-hro.de/dataset/e7c10dd4-d8fb-440c-9fc1-e2649b73e5d7'}
200
________________
1
{'url': 'https://www.opendata-hro.de/dataset/c276228b-9c7b-4812-b4a5-7480316c2233'}
200
________________
2
{'url': 'https://www.opendata-hro.de/dataset/655f46c2-102b-45a6-a9c4-cc7cb56d47df'}
200
________________
3
{'url': 'https://www.opendata-hro.de/dataset/7afdfa7a-7fd4-48a2-be63-e83750eb1c40'}
200
________________
4
{'url': 'https://www.opendata-hro.de/dataset/aceccfc0-dbf2-42a3-9456-389c6a0edb7c'}
200
________________
5
{'url': 'https://www.opendata-hro.de/dataset/8c74c345-92a1-4245-a42a-71c0beef8160'}
200
________________
6
{'url': 'https://www.opendata-hro.de/dataset/b5375466-e593-4a0e-9005-ab6a9bc22395'}
200
________________
7
{'url': 'https://www.opendata-hro.de/dataset/f709d112-a2d1-4098-a8ca-41e364899490'}
200
________________
8
{'url': 'https://www.opendata-hro.de/dataset/7c3a523b-6ef0-46f7-851b-da5340852439'}
200
________________
9
{'url': 'https://www.opendata-hro.d

author  \
0        Hanse- und Universitätsstadt Rostock – Hauptamt   
1      Hanse- und Universitätsstadt Rostock – Kataste...   
2      Hanse- und Universitätsstadt Rostock – Kataste...   
3      Hanse- und Universitätsstadt Rostock – Kataste...   
4        Hanse- und Universitätsstadt Rostock – Hauptamt   
...                                                  ...   
14995                              Verbandsgemeinde Eich   
14996                          Ortsgemeinde Schwedelbach   
14997                      Verbandsgemeinde Altenkirchen   
14998                           Ortsgemeinde Erzenhausen   
14999                      Verbandsgemeinde Altenkirchen   

                     author_email                       creator_user_id  \
0           geodienste@rostock.de  f512f73d-bed2-439d-8f6f-3fbc6048b24e   
1           geodienste@rostock.de  f512f73d-bed2-439d-8f6f-3fbc6048b24e   
2           geodienste@rostock.de  f512f73d-bed2-439d-8f6f-3fbc6048b24e   
3           geodienste@rostock.de  f512f73d-bed2-439d-8f6f-3fbc6048b24e   
4           geodienste@rostock.de  f512f73d-bed2-439d-8f6f-3fbc6048b24e   
...                           ...                                   ...   
14995       poststelle@vg-eich.de  f512f73d-bed2-439d-8f6f-3fbc6048b24e   
14996       info@vg-weilerbach.de  f512f73d-bed2-439d-8f6f-3fbc6048b24e   
14997  rathaus@vg-altenkirchen.de  f512f73d-bed2-439d-8f6f-3fbc6048b24e   
14998       info@vg-weilerbach.de  f512f73d-bed2-439d-8f6f-3fbc6048b24e   
14999  rathaus@vg-altenkirchen.de  f512f73d-bed2-439d-8f6f-3fbc6048b24e   

                                         id  isopen  license_id  \
0      05be0aa5-76a2-4850-b37f-69e623565fbe   False         NaN   
1      44fa7d61-7924-4740-95ec-b4a6821139fe   False         NaN   
2      6219e4c3-e819-40f0-86cd-543ff829ad6c   False         NaN   
3      7c46a2cc-4fe3-4399-8833-61b016730b71   False         NaN   
4      4d25536c-7cc4-4761-8504-0ba8ca320fa1   False         NaN   
...                                     ...     ...         ...   
14995  e725ccc0-5267-4bd0-b81c-32515ab32d8f   False         NaN   
14996  1620d684-d596-46b7-bc24-40250d38a402   False         NaN   
14997  386ee29a-4ee2-4291-8f78-07d163230060   False         NaN   
14998  d4ebb690-762e-4624-864d-d03383a36ada   False         NaN   
14999  1f5edc12-687f-4575-b200-de66968759ae   False         NaN   

       license_title                                         maintainer  \
0                NaN  Hanse- und Universitätsstadt Rostock – Kataste...   
1                NaN  Hanse- und Universitätsstadt Rostock – Kataste...   
2                NaN  Hanse- und Universitätsstadt Rostock – Kataste...   
3                NaN  Hanse- und Universitätsstadt Rostock – Kataste...   
4                NaN  Hanse- und Universitätsstadt Rostock – Kataste...   
...              ...                                                ...   
14995            NaN                                                NaN   
14996            NaN                                                NaN   
14997            NaN                                                NaN   
14998            NaN                                                NaN   
14999            NaN                                                NaN   

            maintainer_email            metadata_created  ...  \
0      geodienste@rostock.de  2023-01-06T06:14:11.920576  ...   
1      geodienste@rostock.de  2024-05-08T06:31:53.940777  ...   
2      geodienste@rostock.de  2024-05-08T06:31:46.141017  ...   
3      geodienste@rostock.de  2024-05-08T06:32:00.483952  ...   
4      geodienste@rostock.de  2024-05-08T06:32:18.276436  ...   
...                      ...                         ...  ...   
14995                    NaN  2022-01-26T10:17:23.776277  ...   
14996                    NaN  2023-08-07T04:51:22.657594  ...   
14997                    NaN  2022-01-26T09:30:21.252167  ...   
14998                    NaN  2023-08-07T04:51:33.293593  ...   
14999  

### Swiss data portal assessment

In [31]:
df = pd.read_csv(r"C:\Users\MolnarM\Downloads\datasets_metadata_switzerland.csv")
df.head()

Unnamed: 0                             owner_org     maintainer  \
0           0  b3d5c5d8-f736-459e-b23b-fe0ea6196cf2  Sara Schärrer   
1           1  348d5b66-0a7b-4ea1-af11-c6c5d926c667            NaN   
2           2  348d5b66-0a7b-4ea1-af11-c6c5d926c667            NaN   
3           3  348d5b66-0a7b-4ea1-af11-c6c5d926c667            NaN   
4           4  348d5b66-0a7b-4ea1-af11-c6c5d926c667            NaN   

                issued                       title_for_slug  \
0  2023-03-02T00:00:00  Tierseuchenmeldungen in der Schweiz   
1  2024-06-18T00:00:00               egid-und-gebaudenummer   
2  2024-06-18T00:00:00                    bodenbedeckung-ur   
3  2024-06-18T00:00:00                         fixpunkte-ur   
4  2024-06-18T00:00:00                     einzelobjekte-ur   

  qualified_relations  private             maintainer_email  num_tags  \
0                  []    False  sara.schaerrer@blv.admin.ch         9   
1                  []    False                          NaN         0   
2                  []    False                          NaN         0   
3                  []    False                          NaN         0   
4                  []    False                          NaN         0   

                                      contact_points  ...  \
0  [{'name': 'Kompetenzzentrum Daten', 'email': '...  ...   
1  [{'email': 'mail@lisag.ch', 'name': 'mail@lisa...  ...   
2  [{'email': 'mail@lisag.ch', 'name': 'mail@lisa...  ...   
3  [{'email': 'mail@lisag.ch', 'name': 'mail@lisa...  ...   
4  [{'email': 'mail@lisag.ch', 'name': 'mail@lisa...  ...   

                                 accrual_periodicity documentation  \
0  http://publications.europa.eu/resource/authori...            []   
1                                                NaN           NaN   
2                                                NaN           NaN   
3                                                NaN           NaN   
4                                                NaN           NaN   

              modified                           url see_alsos  \
0                  NaN  https://infosm.blv.admin.ch/        []   
1  2024-06-18T00:00:00                           NaN        []   
2  2024-06-18T00:00:00                           NaN        []   
3  2024-06-18T00:00:00                           NaN        []   
4  2024-06-18T00:00:00                           NaN        []   

                            revision_id  \
0  c8793a79-b0ff-4e59-98bc-0dec70e90e88   
1  356c93af-2b9b-46d1-9419-b40a4b6cd403   
2  f42e0bb1-5f47-4796-953d-e3d99c8b4fbf   
3  319eb659-a9db-4329-9c4c-21fcca8107c2   
4  ffafc0fa-e71c-4b0e-98f2-18385b406109   

                                          identifier             spatial  \
0  tierseuchen@bundesamt-fur-lebensmittelsicherhe...                 NaN   
1                  ur-1816@geoinformation-kanton-uri  Canton of Uri (UR)   
2                  ur-1718@geoinformation-kanton-uri  Canton of Uri (UR)   
3                  ur-1717@geoinformation-kanton-uri  Canton of Uri (UR)   
4                  ur-1719@geoinformation-kanton-uri  Canton of Uri (UR)   

  coverage                                             extras  
0      NaN                                                NaN  
1      NaN  [{'key': 'harvest_object_id', 'value': 'b1a93d...  
2      NaN  [{'key': 'harvest_object_id', 'value': 'd4ce3d...  
3      NaN  [{'key': 'harvest_object_id', 'value': 'f4b8a6...  
4      NaN  [{'key': 'harvest_object_id', 'value': 'c6c2f2...  

[5 rows x 50 columns]

In [32]:
df.url.tolist()

['https://infosm.blv.admin.ch/',
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 'https://data.geo.so.ch?filter=ch.so.afu.klimaanalyse.windgeschwindigkeit_4uhr_zukunft',
 'https://data.geo.so.ch?filter=ch.so.agi.av.gebaedeflaechen',
 'https://data.geo.so.ch?filter=ch.so.avt.kantonsstrassen',
 nan,
 'https://stadt.winterthur.ch/themen/die-stadt/winterthur/statistik/wirtschaft',
 'https://stadt.winterthur.ch/themen/die-stadt/winterthur/statistik/bauen-und-wohnen',
 'https://stadt.winterthur.ch/themen/die-stadt/winterthur/statistik/bauen-und-wohnen',
 nan,
 'https://stadt.winterthur.ch/themen/die-stadt/winterthur/statistik/bevoelkerung',
 'https://stadt.winterthur.ch/themen/die-stadt/winterthur/statistik/bevoelkerung',
 'https://stadt.winterthur.ch/themen/die-stadt/winterthur/statistik/bevoelkerung',
 'https://stadt.winterthur.ch/themen/die-stadt/winterthur/statistik/wirtschaft',
 'https://sta

In [21]:
for i in df.url.tolist():
    if i != 'nan':
        print(i)

https://infosm.blv.admin.ch/
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
https://data.geo.so.ch?filter=ch.so.afu.klimaanalyse.windgeschwindigkeit_4uhr_zukunft
https://data.geo.so.ch?filter=ch.so.agi.av.gebaedeflaechen
https://data.geo.so.ch?filter=ch.so.avt.kantonsstrassen
nan
https://stadt.winterthur.ch/themen/die-stadt/winterthur/statistik/wirtschaft
https://stadt.winterthur.ch/themen/die-stadt/winterthur/statistik/bauen-und-wohnen
https://stadt.winterthur.ch/themen/die-stadt/winterthur/statistik/bauen-und-wohnen
nan
https://stadt.winterthur.ch/themen/die-stadt/winterthur/statistik/bevoelkerung
https://stadt.winterthur.ch/themen/die-stadt/winterthur/statistik/bevoelkerung
https://stadt.winterthur.ch/themen/die-stadt/winterthur/statistik/bevoelkerung
https://stadt.winterthur.ch/themen/die-stadt/winterthur/statistik/wirtschaft
https://stadt.winterthur.ch/themen/die-stadt/winterthur/statistik/bevoelkerung
https://stadt.winterthur.ch/th

In [22]:
count = 0
assessment_results = df['url'].map(lambda x: get_all_metrics(payload={'url': x}))
df['FAIR_assessment'] = [aresult[0] for aresult in assessment_results]
df['assessment_status_code'] = [aresult[1] for aresult in assessment_results]
df.to_csv(r"C:\Users\MolnarM\Desktop\Notebooks\Uni\ogdmetadatendatagvat_assessed_swiss"+date+".csv", encoding='utf-8')
df

0
{'url': 'https://infosm.blv.admin.ch/'}
200
________________
1
{'url': nan}
500
________________
2
{'url': nan}
500
________________
3
{'url': nan}
500
________________
4
{'url': nan}
500
________________
5
{'url': nan}
500
________________
6
{'url': nan}
500
________________
7
{'url': nan}
500
________________
8
{'url': nan}
500
________________
9
{'url': nan}
500
________________
10
{'url': nan}
500
________________
11
{'url': nan}
500
________________
12
{'url': nan}
500
________________
13
{'url': nan}
500
________________
14
{'url': nan}
500
________________
15
{'url': nan}
500
________________
16
{'url': nan}
500
________________
17
{'url': nan}
500
________________
18
{'url': nan}
500
________________
19
{'url': nan}
500
________________
20
{'url': nan}
500
________________
21
{'url': nan}
500
________________
22
{'url': nan}
500
________________
23
{'url': nan}
500
________________
24
{'url': nan}
500
________________
25
{'url': 'https://data.geo.so.ch?filter=ch.so.afu.klimaa

Unnamed: 0                             owner_org        maintainer  \
0               0  b3d5c5d8-f736-459e-b23b-fe0ea6196cf2     Sara Schärrer   
1               1  348d5b66-0a7b-4ea1-af11-c6c5d926c667               NaN   
2               2  348d5b66-0a7b-4ea1-af11-c6c5d926c667               NaN   
3               3  348d5b66-0a7b-4ea1-af11-c6c5d926c667               NaN   
4               4  348d5b66-0a7b-4ea1-af11-c6c5d926c667               NaN   
...           ...                                   ...               ...   
11887       11887  1e4cc1ec-05f2-4801-821e-492a8199dced               NaN   
11888       11888  1e4cc1ec-05f2-4801-821e-492a8199dced               NaN   
11889       11889  1e4cc1ec-05f2-4801-821e-492a8199dced               NaN   
11890       11890  1e4cc1ec-05f2-4801-821e-492a8199dced               NaN   
11891       11891  6c1b8763-a767-40a4-993c-fc515db2e28c  Open Data Zürich   

                    issued                                     title_for_slug  \
0      2023-03-02T00:00:00                Tierseuchenmeldungen in der Schweiz   
1      2024-06-18T00:00:00                             egid-und-gebaudenummer   
2      2024-06-18T00:00:00                                  bodenbedeckung-ur   
3      2024-06-18T00:00:00                                       fixpunkte-ur   
4      2024-06-18T00:00:00                                   einzelobjekte-ur   
...                    ...                                                ...   
11887  2023-01-18T00:00:00         administrative-einteilung-av-und-grundbuch   
11888  2023-03-01T00:00:00                                       strassenlarm   
11889  2023-02-08T00:00:00                                 orthofoto-2012-rgb   
11890  2023-03-01T00:00:00                                      waldwanderung   
11891  2020-10-30T00:00:00  kapazitat-bestand-reserve-und-inanspruchnahme-...   

      qualified_relations  private             maintainer_email  num_tags  \
0                      []    False  sara.schaerrer@blv.admin.ch         9   
1                      []    False                          NaN         0   
2                      []    False                          NaN         0   
3                      []    False                          NaN         0   
4                      []    False                          NaN         0   
...                   ...      ...                          ...       ...   
11887                 NaN    False                          NaN         0   
11888                 NaN    False                          NaN         0   
11889                 NaN    False                          NaN         0   
11890                 NaN    False                          NaN         0   
11891                 NaN    False          opendata@zuerich.ch         5   

                                          contact_points  ...  \
0      [{'name': 'Kompetenzzentrum Daten', 'email': '...  ...   
1      [{'email': 'mail@lisag.ch', 'name': 'mail@lisa...  ...   
2      [{'email': 'mail@lisag.ch', 'name': 'mail@lisa...  ...   
3      [{'email': 'mail@lisag.ch', 'name': 'mail@lisa...  ...   
4      [{'email': 'mail@lisag.ch', 'name': 'mail@lisa...  ...   
...                                                  ...  ...   
11887  [{'email': 'agi@bd.so.ch', 'name': 'agi@bd.so....  ...   
11888  [{'email': 'avt@bd.so.ch', 'name': 'avt@bd.so....  ...   
11889  [{'email': 'agi@bd.so.ch', 'name': 'agi@bd.so....  ...   
11890  [{'email': 'awjf@vd.so.ch', 'name': 'awjf@vd.s...  ...   
11891  [{'email': 'opendata@zuerich.ch', 'name': 'Ope...  ...   

                  modified                                                url  \
0                      NaN                       https://infosm.blv.admin.ch/   
1      2024-06-18T00:00:00                                                NaN   
2      2024-06-18T00:00:00                                                NaN   
3      2024-06-18T00:00:00                                                NaN  

### Irish data portal assessment

In [33]:
df = pd.read_csv(r"C:\Users\MolnarM\Downloads\datasets_metadata_ireland.csv")
df.head()

author author_email               conforms_to            contact_email  \
0    NaN          NaN                       NaN                      NaN   
1    NaN          NaN                       NaN       opendata@tailte.ie   
2    NaN          NaN                       NaN          opendata@met.ie   
3    NaN          NaN  swagger 2.0, Akoma Ntoso  open.data@oireachtas.ie   
4    NaN          NaN                       NaN                      NaN   

                contact_name contact_phone  \
0                        NaN           NaN   
1                        NaN           NaN   
2              Kieran Harper           NaN   
3  Open Data Liaison Officer  (01) 6183000   
4                        NaN           NaN   

                        creator_user_id             frequency  \
0  0863c6bf-d7d8-485b-94b7-d50a11d5796d            Continuous   
1  f98da442-3307-463d-b676-a327e93755ec            Continuous   
2  f1eafd65-adc1-4721-aefc-fa9b6c9b3a0c            Continuous   
3  ef08264c-676d-48c5-aaad-6ce8aa18d521  Continuously updated   
4  ef08264c-676d-48c5-aaad-6ce8aa18d521                Weekly   

                                     id  isopen  ... high_value_dataset  \
0  f2d3c4fc-0ea7-4959-98c5-598241a5ea51    True  ...                NaN   
1  6eccd685-3dec-481b-9b9f-3f957ba9ddcd    True  ...                NaN   
2  0a8b1aa8-f49b-411e-a120-b0cd0297c2a1    True  ...                NaN   
3  d9ddc7ee-d497-41bb-924f-3557cfa12037    True  ...                NaN   
4  18020dbe-8565-47d0-8632-a8fc4dc540a0    True  ...                NaN   

                                    notes_translated  \
0                                                NaN   
1  {'en': 'The REST Web Services API provides a R...   
2                               {'en': '', 'ga': ''}   
3                                                NaN   
4                                                NaN   

                                    title_translated      issued     updated  \
0                                                NaN         NaN         NaN   
1   {'en': 'Tailte Éireann Valuation API', 'ga': ''}         NaN         NaN   
2  {'en': 'Met Eireann Live Text Forecast Data', ...  2019-03-11  2021-05-17   
3                                                NaN  2017-10-23  2017-10-23   
4                                                NaN  2017-10-06         NaN   

  collection_name temporal_start extras temporal_end expiration_date  
0             NaN            NaN    NaN          NaN             NaN  
1             NaN            NaN    NaN          NaN             NaN  
2             NaN            NaN    NaN          NaN             NaN  
3           adhoc     1919-01-22    NaN          NaN             NaN  
4             NaN     2010-01-01    NaN          NaN             NaN  

[5 rows x 56 columns]

In [35]:
count = 0
assessment_results = df['url'].map(lambda x: get_all_metrics(payload={'url': x}))
df['FAIR_assessment'] = [aresult[0] for aresult in assessment_results]
df['assessment_status_code'] = [aresult[1] for aresult in assessment_results]
df.to_csv(r"C:\Users\MolnarM\Desktop\Notebooks\Uni\ogdmetadatendatagvat_assessed_irish"+date+".csv", encoding='utf-8')
df

0
{'url': 'http://data.geohive.ie/covidData.html'}
200
________________
1
{'url': 'https://www.tailte.ie/en/valuation/open-data/api/'}
200
________________
2
{'url': 'https://www.met.ie/'}
200
________________
3
{'url': 'https://api.oireachtas.ie'}
200
________________
4
{'url': 'https://services.arcgis.com/NzlPQPKn5QF9v2US/arcgis/rest/services/IrishPlanningApplications/FeatureServer'}
200
________________
5
{'url': nan}
500
________________
6
{'url': nan}
500
________________
7
{'url': nan}
500
________________
8
{'url': nan}
500
________________
9
{'url': 'https://data-housinggovie.opendata.arcgis.com/maps/housinggovie::tier2a-planning-applications'}
200
________________
10
{'url': 'https://data-housinggovie.opendata.arcgis.com/maps/housinggovie::tier1-planning-permissions'}
200
________________
11
{'url': nan}
500
________________
12
{'url': 'https://data-housinggovie.opendata.arcgis.com/maps/housinggovie::housing-supply-coordination-task-force-for-dublin-data-q1-2024'}
200
________

author author_email               conforms_to            contact_email  \
0        NaN          NaN                       NaN                      NaN   
1        NaN          NaN                       NaN       opendata@tailte.ie   
2        NaN          NaN                       NaN          opendata@met.ie   
3        NaN          NaN  swagger 2.0, Akoma Ntoso  open.data@oireachtas.ie   
4        NaN          NaN                       NaN                      NaN   
...      ...          ...                       ...                      ...   
14995    NaN          NaN                       NaN                      NaN   
14996    NaN          NaN                       NaN                      NaN   
14997    NaN          NaN                       NaN                      NaN   
14998    NaN          NaN                       NaN                      NaN   
14999    NaN          NaN                       NaN                      NaN   

                    contact_name contact_phone  \
0                            NaN           NaN   
1                            NaN           NaN   
2                  Kieran Harper           NaN   
3      Open Data Liaison Officer  (01) 6183000   
4                            NaN           NaN   
...                          ...           ...   
14995                        NaN           NaN   
14996                        NaN           NaN   
14997                        NaN           NaN   
14998                        NaN           NaN   
14999                        NaN           NaN   

                            creator_user_id             frequency  \
0      0863c6bf-d7d8-485b-94b7-d50a11d5796d            Continuous   
1      f98da442-3307-463d-b676-a327e93755ec            Continuous   
2      f1eafd65-adc1-4721-aefc-fa9b6c9b3a0c            Continuous   
3      ef08264c-676d-48c5-aaad-6ce8aa18d521  Continuously updated   
4      ef08264c-676d-48c5-aaad-6ce8aa18d521                Weekly   
...                                     ...                   ...   
14995  ef08264c-676d-48c5-aaad-6ce8aa18d521              Biennial   
14996  ef08264c-676d-48c5-aaad-6ce8aa18d521              Biennial   
14997  ef08264c-676d-48c5-aaad-6ce8aa18d521               Monthly   
14998  ef08264c-676d-48c5-aaad-6ce8aa18d521               Monthly   
14999  ef08264c-676d-48c5-aaad-6ce8aa18d521               Monthly   

                                         id  isopen  ...  \
0      f2d3c4fc-0ea7-4959-98c5-598241a5ea51    True  ...   
1      6eccd685-3dec-481b-9b9f-3f957ba9ddcd    True  ...   
2      0a8b1aa8-f49b-411e-a120-b0cd0297c2a1    True  ...   
3      d9ddc7ee-d497-41bb-924f-3557cfa12037    True  ...   
4      18020dbe-8565-47d0-8632-a8fc4dc540a0    True  ...   
...                                     ...     ...  ...   
14995  4ad8dcfe-5fe3-48d7-929c-57dc33e94b75    True  ...   
14996  4a4e7441-b10a-420b-b836-fe147e88df7f    True  ...   
14997  4a47ca32-68bd-4165-a383-caa68a90796e    True  ...   
14998  4a1a978b-0ba0-461a-83e5-9bc217c20bd2    True  ...   
14999  49ef9e86-afa0-4230-a295-138a5ec82d12    True  ...   

                                        title_translated      issued  \
0                                                    NaN         NaN   
1       {'en': 'Tailte Éireann Valuation API', 'ga': ''}         NaN   
2      {'en': 'Met Eireann Live Text Forecast Data', ...  2019-03-11   
3                                                    NaN  2017-10-23   
4                                                    NaN  2017-10-06   
...                                                  ...         ...   
14995  {'en': 'No. of Meitheal Processes Requested vi...         NaN   
14996  {'en': 'No. of Children Referred to Family Sup...         NaN   
14997  {'en': 'No. of Individual Children School Atte...         NaN   
14998  {'en': 'No. of Children in Residential General...         NaN   
14999  {'en': 'No. of Court Cases where Educational W...         NaN   

          updated collection_